In [2]:
import os 
from transformers import AutoConfig, AutoTokenizer, AutoModelForSequenceClassification, DataCollatorWithPadding

In [3]:
model_name_or_path = "/datadrive/namlh31/codebridge/Codebert-docstring-inconsistency"
config = AutoConfig.from_pretrained(
 model_name_or_path,
)
tokenizer = AutoTokenizer.from_pretrained(
    model_name_or_path
)
model = AutoModelForSequenceClassification.from_pretrained(
model_name_or_path,
config=config,
)

In [5]:
examples = {'code': "function(str){\r\n  var ret = new Array(str.length), len = str.length;\r\n  while(len--) ret[len] = str.charCodeAt(len);\r\n  return Uint8Array.from(ret);\r\n}",
            'docstring': 'we do not need Buffer pollyfill for now'}

In [17]:
texts = (
        (examples['docstring'], examples['code'])
    )
result = tokenizer(*texts, padding="max_length", max_length=512, truncation=True, return_tensors= 'pt')

In [10]:
tokenizer.decode(result['input_ids'])
print(len(result['input_ids']))

512


In [22]:
input = """we do not need Buffer pollyfill for now</s></s>function(str){\r\n  var ret = new Array(str.length), len = str.length;\r\n  while(len--) ret[len] = str.charCodeAt(len);\r\n  return Uint8Array.from(ret);\r\n}"""
rs_2 = tokenizer(input, padding="max_length", max_length=512, truncation=True, return_tensors= 'pt')

In [23]:
model(**rs_2)

SequenceClassifierOutput(loss=None, logits=tensor([[ 0.2598, -0.2636]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [24]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline
import torch
device = 0 if torch.cuda.is_available() else -1
pipeline = pipeline("text-classification", model=model, tokenizer=tokenizer, device=device)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [28]:
inputs = """we do not need Buffer pollyfill for now</s></s>function(str){
  var ret = new Array(str.length), len = str.length;
  while(len--) ret[len] = str.charCodeAt(len);
  return Uint8Array.from(ret);
}"""
prediction = pipeline(inputs)
print(prediction)

[{'label': 'Inconsistency', 'score': 0.5601343512535095}]
